<a href="https://colab.research.google.com/github/dyou-wbg/meta_processing/blob/main/All_Except_SemanticScholar_faster__char_based_distance_knn_deduping.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
from google.colab import drive
drive.mount('/content/drive')
import pandas as pd
from google.colab import drive
import csv
import os
import re
import pandas as pd
import numpy as np

directory = '/content/drive/MyDrive/finalMetaFile'

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
final_file_list = ['metadata_jstor.csv',
                   'elsevier_metadata.csv',
                   'scopus_fixed_encoding.csv',
                   'url1_ie_table_complete.csv',
                   'metadata_econlit.csv',
                   'SSRN_metadata.csv',
                   'metadata_repec.csv',
                   'scopus_fixed_encoding.csv']

for filename in final_file_list:
    if os.path.isfile(os.path.join(directory, filename)) and filename.endswith(".csv"):
        df = pd.read_csv(os.path.join(directory, filename))
        if "title" in df.columns:
            print(filename,len(df))
        elif 'doc_name' in df.columns:
            print(filename,len(df))





* url1_ie_table_complete.csv       11,377
* metadata_econlit.csv             19,121
* SSRN_metadata.csv                99,106
* elsevier_metadata.csv           242,410
* metadata_repec.csv              915,771
* scopus_fixed_encoding           961,490
* metadata_jstor.csv            1,095,398
* metadata_semantic_scholar.csv 7,912,377


In [4]:
# 7 sources. dropped NBER
final_file_list = ['metadata_jstor.csv',
                   'elsevier_metadata.csv',
                   'scopus_fixed_encoding.csv',
                   'url1_ie_table_complete.csv',
                   'metadata_econlit.csv',
                   'SSRN_metadata.csv',
                   'metadata_repec.csv']

dataframes = []

for filename in final_file_list:
    if os.path.isfile(os.path.join(directory, filename)) and filename.endswith(".csv"):
        df = pd.read_csv(os.path.join(directory, filename))
        if "title" in df.columns:
            df_final = df['title']
        elif 'doc_name' in df.columns:
            df_final = df['doc_name']
        else:
            print(f"Missing required column in file: {filename}")
            continue
        dataframes.append(df_final)

df_combined = pd.concat(dataframes, ignore_index=True)


<ipython-input-4-65eae42e35ff>:14: DtypeWarning: Columns (11) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(os.path.join(directory, filename))
<ipython-input-4-65eae42e35ff>:14: DtypeWarning: Columns (4,7) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(os.path.join(directory, filename))


In [5]:
df=pd.DataFrame(df_combined)
df.rename(columns={0: 'title'}, inplace=True)
#df.drop(columns=['Unnamed: 0'], inplace=True)
df.head()

title
0  Economic Education in Our Schools: A Renewed M...
1                 Can Germany Contain Russia Safely?
2  Assessing the Impact of Sarbanes-Oxley Act on ...
3  Childhood Educational Disruption and Later Lif...
4          The Exclusion of Liability for Negligence

In [6]:
df.columns

Index(['title'], dtype='object')

In [13]:
len(df)

3316876

In [8]:
df.to_csv('/content/drive/MyDrive/All_but_semanticScholar_titles.csv')

In [14]:
df = df.dropna()
df.head()

title
0  Economic Education in Our Schools: A Renewed M...
1                 Can Germany Contain Russia Safely?
2  Assessing the Impact of Sarbanes-Oxley Act on ...
3  Childhood Educational Disruption and Later Lif...
4          The Exclusion of Liability for Negligence

In [10]:
#ng
%%time
from string import printable
from collections import Counter

printable_dict = {c:i for i,c in enumerate(printable)}


def vectorize(title):
    """ Returns a vector with counts for each printable character found in a title """
    cnt = Counter(title)
    array = [0 for _ in printable]+[0] # Last position is for nonprintable characters
    for c,n in cnt.items():
        if c in printable_dict:
            array[printable_dict[c]]=n
        else:
            array[-1]+=n # Update last position if it's not printable
    return np.array(array)

vects = []
for title in df.title:
    vects.append(vectorize(title))

CPU times: user 45.8 s, sys: 3.73 s, total: 49.5 s
Wall time: 49.5 s


In [ ]:
#g
%%time
unique_vects, indices, counts = np.unique(vects, axis=0, return_index=True, return_counts=True)

duplicate_indices = indices[counts > 1]

if len(duplicate_indices) > 0:
    print("Duplicate titles found!")
    for idx in duplicate_indices:
        print(f"Duplicate title vector: {vects[idx]}")
else:
    print("No duplicate titles found.")

In [38]:
duplicate_indices = indices[counts > 1]

In [39]:
duplicate_indices

array([ 107789,  158574, 2568119, ..., 2012710, 1441592, 1863176])

In [16]:
#g

for idx in duplicate_indices:
    print(f"Duplicate title: {df['title'].iloc[idx]}")


Streaming output truncated to the last 5000 lines.
Duplicate title: Projektion des Angebots an inländischen Arbeitskräften in der Bundesrepublik Deutschland für die Jahre 1973, 1975 und 1980
Duplicate title: Mutual benefit societies in Hungary, 1830‐1941
Duplicate title: Was there an urban height penalty in Spain, 1840-1913?
Duplicate title: Land abundance and economic institutions: Egba land and slavery, 1830-1914
Duplicate title: Ocean Freight Rates and Productivity, 1740-1913: The Primacy of Mechanical Invention Reaffirmed
Duplicate title: Interstate Differences In Economic Growth Rates In Australia, 1953-54 to 1990-91
Duplicate title: A Cost-Effectiveness Analysis of the 10-Valent Pneumococcal Non-Typeable Haemophilus influenzae Protein D Conjugate Vaccine (PHiD-CV) Compared to the 13-Valent Pneumococcal Conjugate Vaccine (PCV13) for Universal Mass Vaccination Implementation in New Zealand
Duplicate title: Quellen und materialien: Wirtschaftsbesprechungen der NSDAP in den Jahren 19

In [18]:
duplicate_indices


array([ 107789,  158574, 2568119, ..., 2012710, 1441592, 1863176])

In [19]:

df[df['title']=='Bubble diagnosis and prediction of the 2005-2007 and 2008-2009 Chinese stock market bubbles']


title
1283876  Bubble diagnosis and prediction of the 2005-20...
1605733  Bubble diagnosis and prediction of the 2005-20...

In [20]:
# prompt: Delete titles that belongs to duplicate_indices

df = df.drop(duplicate_indices)


KeyError: '[2447178, 2447195, 2447214, 2447182, 2447181, 2447204, 2520982, 2454088, 2582731, 2582845, 2454087, 2632176, 2449480, 2632157, 2532243, 2454089, 2713069, 2632165, 2632166, 2632179, 2632160, 2585489, 2454107, 2532254, 2454114, 2429102, 2431719, 2485645, 2683419, 2437507, 2592785, 2437503, 2431696, 2539749, 2437546, 2716746, 2437545, 2437518, 2429167, 2539717, 2539716, 2669898, 2431742, 2714117, 2539855, 2485654, 2447529, 2431686, 2431804, 2430025, 2714139, 2591551, 2669859, 2930113, 2521057, 2696847, 2537720, 2907012, 2671977, 2933589, 2607037, 2604730, 2511577, 2591865, 2696881, 2862772, 2562167, 2528818, 2916842, 2754355, 2534403, 2508429, 2935206, 2607064, 2875096, 2535427, 2926427, 2659632, 2508422, 2590786, 2585027, 3057392, 2933569, 2669459, 2429166, 2669830, 2597106, 2607047, 2492970, 2753336, 2906021, 2497784, 2934836, 2508403, 2671985, 2752263, 2429122, 2787742, 2429420, 2534739, 2589957, 2534383, 2860014, 2591266, 3057255, 2582810, 2985023, 2446929, 2508405, 2429291

In [21]:
duplicate_indices.shape


(350530,)

In [22]:
df.index

Int64Index([      0,       1,       2,       3,       4,       5,       6,
                  7,       8,       9,
            ...
            3344663, 3344664, 3344665, 3344666, 3344667, 3344668, 3344669,
            3344670, 3344671, 3344672],
           dtype='int64', length=3316876)

In [23]:
df.index.values

array([      0,       1,       2, ..., 3344670, 3344671, 3344672])

In [37]:
duplicate_indices

['107789',
 '158574',
 '2568119',
 '2568056',
 '2485528',
 '2568078',
 '2282638',
 '2568326',
 '2452717',
 '2452713',
 '2447178',
 '2452715',
 '2452716',
 '2447195',
 '2568435',
 '2568047',
 '2447214',
 '2568002',
 '2447182',
 '2452722',
 '2447181',
 '2568388',
 '2581707',
 '2568147',
 '2452720',
 '2568132',
 '2568289',
 '2447204',
 '2642984',
 '2568355',
 '2452712',
 '2568034',
 '2662701',
 '2568384',
 '2576190',
 '2568340',
 '2452709',
 '2731757',
 '2731736',
 '2568507',
 '2582264',
 '123490',
 '125193',
 '122366',
 '131972',
 '114854',
 '129402',
 '101447',
 '123273',
 '134887',
 '142488',
 '151476',
 '2551034',
 '2838894',
 '2465069',
 '2464869',
 '2520982',
 '2741564',
 '2905363',
 '2575611',
 '2568390',
 '2576558',
 '2873336',
 '2821009',
 '2464894',
 '130990',
 '113458',
 '268046',
 '144873',
 '101440',
 '117166',
 '153827',
 '101742',
 '100175',
 '145499',
 '128305',
 '2550973',
 '2464856',
 '2954264',
 '2465245',
 '133497',
 '2583630',
 '2486650',
 '2464942',
 '2644927',
 '246

In [25]:
df_deduped = df.drop(index=duplicate_indices)

KeyError: '[2447178, 2447195, 2447214, 2447182, 2447181, 2447204, 2520982, 2454088, 2582731, 2582845, 2454087, 2632176, 2449480, 2632157, 2532243, 2454089, 2713069, 2632165, 2632166, 2632179, 2632160, 2585489, 2454107, 2532254, 2454114, 2429102, 2431719, 2485645, 2683419, 2437507, 2592785, 2437503, 2431696, 2539749, 2437546, 2716746, 2437545, 2437518, 2429167, 2539717, 2539716, 2669898, 2431742, 2714117, 2539855, 2485654, 2447529, 2431686, 2431804, 2430025, 2714139, 2591551, 2669859, 2930113, 2521057, 2696847, 2537720, 2907012, 2671977, 2933589, 2607037, 2604730, 2511577, 2591865, 2696881, 2862772, 2562167, 2528818, 2916842, 2754355, 2534403, 2508429, 2935206, 2607064, 2875096, 2535427, 2926427, 2659632, 2508422, 2590786, 2585027, 3057392, 2933569, 2669459, 2429166, 2669830, 2597106, 2607047, 2492970, 2753336, 2906021, 2497784, 2934836, 2508403, 2671985, 2752263, 2429122, 2787742, 2429420, 2534739, 2589957, 2534383, 2860014, 2591266, 3057255, 2582810, 2985023, 2446929, 2508405, 2429291

In [27]:
duplicate_indices = [str(index) for index in duplicate_indices]
df_deduped = df.drop(index=duplicate_indices)

KeyError: "['107789', '158574', '2568119', '2568056', '2485528', '2568078', '2282638', '2568326', '2452717', '2452713', '2447178', '2452715', '2452716', '2447195', '2568435', '2568047', '2447214', '2568002', '2447182', '2452722', '2447181', '2568388', '2581707', '2568147', '2452720', '2568132', '2568289', '2447204', '2642984', '2568355', '2452712', '2568034', '2662701', '2568384', '2576190', '2568340', '2452709', '2731757', '2731736', '2568507', '2582264', '123490', '125193', '122366', '131972', '114854', '129402', '101447', '123273', '134887', '142488', '151476', '2551034', '2838894', '2465069', '2464869', '2520982', '2741564', '2905363', '2575611', '2568390', '2576558', '2873336', '2821009', '2464894', '130990', '113458', '268046', '144873', '101440', '117166', '153827', '101742', '100175', '145499', '128305', '2550973', '2464856', '2954264', '2465245', '133497', '2583630', '2486650', '2464942', '2644927', '2464857', '108093', '2454088', '114163', '113858', '126420', '143238', '10719

In [ ]:
# prompt: drop title when index is equal to duplicate_indices

df_deduped = df.drop(index=duplicate_indices)


In [40]:
# prompt: show when df index is 3344672

print(df.iloc[1863176])


title    Erratum: Macro- and micro economic impacts of ...
Name: 1863194, dtype: object


In [41]:

print(len(duplicate_indices))


350530


From 3M sources (= 7 sources excluding semantic search)
350k are duplicated.
Took around 15min with 25GB ram
Need to check false positive cases.

But more importantly,
1. Need to check what to do with non-english articles
2. Many of them are "editorial" or list of abbreviations or irrelevant such as patent and so on.

In [ ]:
%%time
from sklearn.neighbors import KDTree

threshold = 10
min_length = 20

tree = KDTree(np.array(vects), leaf_size=10, metric='cityblock')

for i, v1 in enumerate(vects):
    if sum(v1[:-1]) > min_length:
        # Find all vectors within the threshold distance of v1
        indices = tree.query_radius(v1.reshape(1, -1), threshold)[0]
        # Extract the corresponding titles from the retrieved indices
        for j in indices:
            if i != j:
                t1 = df.iloc[i].title
                t2 = df.iloc[j].title
                # Print the potential duplicate titles along with a separator
                print(t1)
                print(t2)
                print('_' * 100)

In [33]:
def vectorize_all(titles):
    cnt_matrix = np.zeros((len(titles), len(printable_dict) + 1), dtype=int)
    for i, title in enumerate(titles):
        cnt = Counter(title)
        for c, n in cnt.items():
            if c in printable_dict:
                cnt_matrix[i, printable_dict[c]] = n
            else:
                cnt_matrix[i, -1] += n
    return cnt_matrix

vects = vectorize_all(df.title)

In [39]:
from scipy.spatial import distance_matrix
threshold = 10
min_length = 20

In [40]:
vects_df = pd.DataFrame(vects)

In [41]:
lengths = vects_df.sum(axis=1)

In [42]:
filtered_indices = lengths[lengths > min_length].index

In [43]:
filtered_vects = vects_df.loc[filtered_indices]

In [ ]:
%%time
distances = distance_matrix(filtered_vects.values[:, :-1], filtered_vects.values[:, :-1], p=1)


In [ ]:

for i, j in zip(*np.where(distances < threshold)):
    if i != j:
        t1 = df.iloc[filtered_indices[i]].title
        t2 = df.iloc[filtered_indices[j]].title
        print(t1)
        print(t2)
        print('_' * 100)

In [ ]:

compared_titles = []
for i, j in zip(*np.where(distances < threshold)):
    if i != j:
        t1 = df.iloc[filtered_indices[i]].title
        t2 = df.iloc[filtered_indices[j]].title
        compared_titles.append([t1, t2])




In [ ]:
df.to_csv('/content/drive/MyDrive/All_but_semanticScholar_titles.csv')